In [1]:
# Import libraries
import datetime
import io
import zipfile
from pathlib import Path
import folium
from folium.plugins import Geocoder
import geopandas as gpd
import numpy as np
import pandas as pd

**AO Transport Recommendations**

- *Rideshare and taxi patrons* will use the designated drop-off and pick-up location outside the *Grand Slam Oval entrance on Olympic Boulevard*.

- *Taxi patrons* may also be dropped off and picked up at the *Flinders Street Station taxi rank*.

- Patrons travelling by *car* can park at *Yarra Park*.

In [2]:
# Read traffic site geojson file
traffic_gdf = gpd.read_file("../data/Traffic_Lights.geojson")

# Create map
map = folium.Map(
    location=[traffic_gdf.geometry.y.mean(), traffic_gdf.geometry.x.mean()],
    tiles="OpenStreetMap"
)

# Create traffic sites on map
for row in traffic_gdf.itertuples():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=4,
        tooltip=f"Site Number: {row.SITE_NO}, Site Name: {row.SITE_NAME}"
    ).add_to(map)

# Add location search bar 
Geocoder().add_to(map)

map

Based on the AO transport recommendations and traffic site map, the following sites were selected to best represent the traffic generated by AO patrons.

In [3]:
transport_dict = {"Taxi": {"Olympic Boulevard": [3445, 4551], "Flinders Street Station": [4530, 4561, 4563, 4570]},
                  "Rideshare": {"Olympic Boulevard": [3445, 4551]},
                  "Car": {"Yarra Park": [1052, 1586, 3391, 4452]}}

# Collate all sites into a list
site_lst = []
for outer_key in transport_dict.keys():
    for lst in transport_dict[outer_key].values():
        site_lst += lst
site_lst = set(site_lst)

site_lst

{1052, 1586, 3391, 3445, 4452, 4530, 4551, 4561, 4563, 4570}

In [ ]:
# Clean traffic volume data

directory_path = Path("../data")

# Loop through only zip files
for file_path in sorted(directory_path.glob("*.zip")):

    year = int(str(file_path)[-8:-4])
    dfs = []

    with zipfile.ZipFile(file_path) as z1:
        # Loop through each monthly traffic
        for inner_zip_name in z1.namelist():
            with z1.open(inner_zip_name) as inner_zip_file:
                with zipfile.ZipFile(io.BytesIO(inner_zip_file.read())) as z2:
                    # Loop through each daily traffic (sorted)
                    for i, file_name in enumerate(sorted(z2.namelist())):
                        if file_name.lower().endswith(".csv"):
                            with z2.open(file_name) as f:
                                # Read traffic volume file
                                df = pd.read_csv(f)

                                # Filter traffic sites
                                df = df[df["NB_SCATS_SITE"].isin(site_lst)].reset_index(drop=True)

                                # Extract date from filename
                                date_str = file_name[-12:-4]
                                date_obj = datetime.date(
                                    int(date_str[0:4]),
                                    int(date_str[4:6]),
                                    int(date_str[6:8])
                                )

                                # Find weekday based on date
                                weekday = date_obj.weekday()

                                # Add date columns to df
                                df = df.assign(
                                    Year=date_obj.year,
                                    Month=date_obj.month,
                                    Day=date_obj.day,
                                    Weekday=weekday,
                                    Weekday_Y_N=weekday < 5
                                )

                                # Skip header rows after first df
                                dfs.append(df.iloc[1:] if i > 0 else df)
                                print(f"Reading {file_name} complete.")

    # Add joining dfs
    traffic_df = pd.concat(dfs, ignore_index=True).copy()

    # Drop irrelavant columns
    traffic_df.drop(["QT_INTERVAL_COUNT", "QT_VOLUME_24HOUR", "NM_REGION", "CT_ALARM_24HOUR"], axis=1, inplace=True)

    # Rename column names
    traffic_df.rename(columns={
                        "NB_SCATS_SITE": "Site Number",
                        "NB_DETECTOR": "Detector Number",
                        "CT_RECORDS": "Number of Recorded Periods"}, 
                      inplace=True)
    
    volume_cols = traffic_df.columns[2:98]

    # Remove rows with all non-positive volume values
    traffic_df = traffic_df[(traffic_df[volume_cols] > 0).all(axis=1)]

    # Change volume value to int type
    traffic_df[volume_cols] = traffic_df[volume_cols].astype(int)

    # Add total traffic volume column
    traffic_df["Total Traffic Volume"] = traffic_df[volume_cols].sum(axis=1)

    # Sum traffic volume by hour
    hourly_volume = pd.DataFrame()
    j = 1
    for i in range(1, 97, 4):
        hourly_volume[f"Traffic Hour {j}"] = traffic_df.iloc[:, i+5:i+9].sum(axis=1)
        j += 1
    traffic_df.drop(traffic_df[volume_cols], axis=1, inplace=True)
    traffic_df = pd.concat([traffic_df, hourly_volume], axis=1)

    # Sum traffic volume by site and date
    traffic_df = traffic_df.groupby(["Site Number", "Year", "Month", "Day", "Weekday", "Weekday_Y_N"], as_index=False).sum().drop(["Detector Number"], axis=1)

    # Add site name column
    def add_site_name(row):
        for outer_key in transport_dict.keys():
            inner_dict = transport_dict[outer_key]
            for site_name in inner_dict.keys():
                if row["Site Number"] in inner_dict[site_name]:
                    return site_name
                
    traffic_df["Site Name"] = traffic_df.apply(add_site_name, axis=1)

    # Save cleaned dataset
    traffic_df.to_csv(f"../cleaned_data/traffic_volume_{year}.csv", index=False)

Reading VSDATA_202001/VSDATA_20200101.csv complete.
Reading VSDATA_202001/VSDATA_20200102.csv complete.
Reading VSDATA_202001/VSDATA_20200103.csv complete.
Reading VSDATA_202001/VSDATA_20200104.csv complete.
Reading VSDATA_202001/VSDATA_20200105.csv complete.
Reading VSDATA_202001/VSDATA_20200106.csv complete.
Reading VSDATA_202001/VSDATA_20200107.csv complete.
Reading VSDATA_202001/VSDATA_20200108.csv complete.
Reading VSDATA_202001/VSDATA_20200109.csv complete.
Reading VSDATA_202001/VSDATA_20200110.csv complete.
Reading VSDATA_202001/VSDATA_20200111.csv complete.
Reading VSDATA_202001/VSDATA_20200112.csv complete.
Reading VSDATA_202001/VSDATA_20200113.csv complete.
Reading VSDATA_202001/VSDATA_20200114.csv complete.
Reading VSDATA_202001/VSDATA_20200115.csv complete.
Reading VSDATA_202001/VSDATA_20200116.csv complete.
Reading VSDATA_202001/VSDATA_20200117.csv complete.
Reading VSDATA_202001/VSDATA_20200118.csv complete.
Reading VSDATA_202001/VSDATA_20200119.csv complete.
Reading VSDA